## Imports

In [ ]:
from typing import Callable

import torch
import numpy as np
import plotly.io as pio
import plotly.express as px
from torch.optim import AdamW
from rich.progress import track
from pandas import DataFrame as DF
from torch.utils import data as torch_data
from torch.amp import autocast, GradScaler
from torch.utils.data import DataLoader as DL
from torch.optim.lr_scheduler import ExponentialLR, LRScheduler, OneCycleLR

from models import mk_model
from training import fit, evaluate_model
from datasets import TrainValidationPreprocessedOpenFWI as OpenFWIDataset

# Make the plotly plots (mostly) renderable on github.
pio.renderers.default = "jupyterlab+png"

## Datasets and data loaders

In [2]:
train_dataset = OpenFWIDataset("train", nb_files=150)
train_loader = torch_data.DataLoader(train_dataset, batch_size=128, shuffle=True)

Output()

920


Output()

In [3]:
validation_dataset = OpenFWIDataset("validation")
validation_loader = torch_data.DataLoader(train_dataset, batch_size=128, shuffle=True)

Output()

20


Output()

## Training

### Find lr

#### Run mock training

In [5]:
MOCK_TRAINING_EPOCHS = 3
STARTING_LR = 1e-5

mock_model = mk_model()
mock_optim = AdamW(mock_model.parameters(), lr=STARTING_LR)
mock_training_metrics = fit(
    epochs=MOCK_TRAINING_EPOCHS,
    model=mock_model,
    optimizer=mock_optim,
    scheduler=ExponentialLR(mock_optim, 1.01),
    train_loader=train_loader,
)
mock_training_metrics = (
    mock_training_metrics
    .query("batch_train_loss.notna()")
    .set_index("lr")
)

Output()

Output()

Output()

0.3526632018008475


nan


#### Visualize smoothed loss over learning rate

In [6]:
mock_training_metrics["ewm_batch_train_loss"] = (
    mock_training_metrics
    .ewm(com=15, ignore_na=False)
    ["batch_train_loss"]
    .mean()
)

px.line(
    mock_training_metrics,
    y="ewm_batch_train_loss",
    log_x=True,
    log_y=True
)

### Fit model

In [11]:
max_lr = mock_training_metrics["ewm_batch_train_loss"].idxmin() * 2
max_lr


TRAINING_EPOCHS = 4
STEPS_PER_EPOCH = len(mock_training_metrics.query("epoch == 0"))


model = mk_model()
optimizer = AdamW(model.parameters(), lr=max_lr)
scheduler = OneCycleLR(
    optimizer,
    max_lr,
    epochs=TRAINING_EPOCHS,
    steps_per_epoch=STEPS_PER_EPOCH
)
training_metrics = fit(
    TRAINING_EPOCHS,
    model,
    scheduler,
    optimizer,
    train_loader,
    lambda :evaluate_model(model)
)

Output()

Output()

0.3390376721398305


Output()

evaluation: {'test_loss': 0.85419921875}


...

Output()

evaluation: {'test_loss': 0.2163669392213983}


Output()

0.1758567680746822


evaluation: {'test_loss': 0.1535289699748411}


#### Visualize loss over training steps

In [14]:
px.scatter(
    (
        training_metrics
        .reset_index()
        .melt(
            id_vars="index",
            value_vars=["batch_train_loss", "lr", "test_loss"],
        )
    ),
    x="index",
    y="value",
    color="variable",
    facet_row="variable",
    render_mode='lines+markers',
).update_yaxes(matches=None)

#### Save model

In [15]:
! mkdir -p "models"
torch.save(model.state_dict(), "./models/latest_model.pth")

## Visualize trained model's outputs

In [ ]:
OFFSET = 50
IMGS_TO_SHOW = 10

def viz_model_outputs(data_loader: DL):
    x, y = next(iter(data_loader))


    y_true_to_display = (
        y
        .cpu()
        .numpy()
        [OFFSET:OFFSET+IMGS_TO_SHOW, 0, ...]
    )
    with autocast("cuda"):
        y_pred = model(x.cuda())
    y_pred_to_display = (
        y_pred
        .cpu()
        .detach()
        .numpy()
        [OFFSET:OFFSET+IMGS_TO_SHOW, 0, ...]
    )

    px.imshow(
        np.concatenate((
            y_true_to_display,
            y_pred_to_display,
            np.abs(y_pred_to_display - y_true_to_display), # Absolute loss
        )),
        facet_col=0,
        facet_col_wrap=IMGS_TO_SHOW,
        color_continuous_scale="Rainbow",
        height=600,
    ).show()

print('train')
viz_model_outputs(train_loader)
print('test')
viz_model_outputs(validation_loader)

train


test
